# 说明
这是一个对于之前用到的寻找相似新闻功能的实现整理  
参考资料：  
http://www.52nlp.cn/如何计算两个文档的相似度全文文档  
数据：  
此处用搜狗新闻语料作为示例：http://www.sogou.com/labs/resource/ca.php

In [22]:
import pandas as pd
import numpy as np
from datetime import datetime

In [23]:
# 读入新闻数据
df_news = pd.read_table(r'C:\baidu\BaiduNetdisk\DataSet\Sougou New Corpus\train.txt',names=['category','theme','URL','content'],encoding='utf-8')
df_news = df_news.dropna()
df_news.head()

category                 theme  \
0       汽车  现代飞思现金直降８０００元　现车颜色齐全   
1       汽车      丰田皇冠对问题车型实行“暗召回”   
2       汽车     价格战爆发　京城豪华车日子也不好过   
3       汽车  成都车展一神秘女子买走４００万绝版宾利车   
4       汽车   通用和欧宝工会拟１１月之前达成重组协议   

                                                 URL  \
0  http://autos.cn.yahoo.com/ypen/20120610/110144...   
1  http://autos.cn.yahoo.com/ypen/20120615/111456...   
2  http://autos.cn.yahoo.com/ypen/20120612/110681...   
3  http://autos.cn.yahoo.com/newspic/autos2/5363/...   
4  http://autos.cn.yahoo.com/ypen/20120615/111428...   

                                             content  
0  近日，编辑从进口现代合肥地区某经销商处了解到，即日起至６月３０日到该店购买现代飞思现金直降８...  
1  虽然说代表王权的皇冠（车型　配置　图片　报价）并非谁都可以拥有，但皇冠汽车，只要有足够的钞票...  
2  “今年上半年的日子不好过呀！”的确，今年上半年，京城车市并非只是一些自主品牌的日子难熬，之前...  
3  在宾利展厅，下午４点以前，一款车一直没有揭开真面目，覆盖在车身上的天鹅绒幕布更让人感受到这款...  
4  据外媒消息，通用汽车公司与德国金属工业工会拟在１１月份之前就欧宝重组的问题达成明确协议。５鹿...

In [4]:
#看下数据量
df_news.shape

(50000, 4)

In [8]:
df_news.groupby('category')['content'].count()

category
体育    5000
健康    5000
军事    5000
娱乐    5000
教育    5000
文化    5000
时尚    5000
汽车    5000
科技    5000
财经    5000
Name: content, dtype: int64

In [51]:
# 创建停用词列表，以下两种实现方法都会用到
def stopwordslist(filepath):  
    stopwords = [line.strip() for line in open(filepath, 'r',encoding='utf-8').readlines()]  
    # 如果不加encoding='utf-8'会报错
    # UnicodeDecodeError: 'gbk' codec can't decode byte 0xbf in position 2: illegal multibyte sequence
    return stopwords 

In [52]:
stopwords = stopwordslist('stopword_cn.txt')

# 一个简单的实现  
仅用词向量的余弦值比较来查找相似文章，用来对比效果：

In [5]:
from sklearn.feature_extraction.text import CountVectorizer
import jieba

sklearn需要的是空格分隔的语料  
使用jieba分词，构造空格分割的语料, 存入文件以便以避免每次重复构造

In [48]:
def build_corpus(content,writetofile=True, filename = 'words_space_seperated_list.txt' ,delimiter = ' '):
    
    seg_list = jieba.cut(content,cut_all = True)
    #content_words = [w for w in seg_list if w not in stopwords and w != '\t']
    #使用Series的isin过滤stopwords，相比对列表使用for循环判断，时间缩短2/3
    content_words = pd.Series([w for w in seg_list])
    content_words = list(content_words[~content_words.isin(stopwords)])
    
    if writetofile:
        # 写入文件，后续调试不需要再次构造
        with open(filename,'a') as f:
            f.write(delimiter.join(content_words))
            f.write('\n')
                                     
    return content_words

In [118]:
# 构造语料，可跳过直接读取文件内容
import os

filename = 'words_space_seperated_list.txt'

if os.path.exists(filename):
    os.remove(filename)

print(datetime.now())
df_news['content'].apply(build_corpus,args = (True,filename,' '))
print(datetime.now())

2018-04-30 09:26:55.745250
2018-04-30 09:30:52.698023


In [4]:
#从文件中读取list of list
def read_corpus(file, method='listoflist', delimiter = ','):
    result = []
    with open(file,'r') as f:
        for line in f.readlines():
            if method=='list':
                result.append(line)
            else:
                word_list = line.split(delimiter)
                result.append(word_list)

    return result

In [9]:
space_seperated_list = read_corpus('words_space_seperated_list.txt','list')

In [10]:
space_seperated_list[0]

'近日 编辑 进口 合肥 肥地 地区 经销 经销商 处 即日 即日起 起至 月 日 该店 购买 飞 思 现金 直 降 元 店 现 车 充足 颜色 齐全 更多 详情 详情请 咨询 经销 经销商 飞 思 车型 最新 价格 表 伤 汲 敌 妥 钚 录 鄹 癖 浠 表 邢 殖 担 颜色 全 更多 详情 详情请 咨询 经销 经销商 雅科 仕 车型 配置 图片 报价 质保 周期 五年 公里 店 内建 建议 保养 周期 万公里 公里 更换 机油 油机 机滤 费用 元 更换 机油 三滤 费用 元 保养 信息 当天 店 保养 信息 为准 嗉 点评 口 雅科 仕 一款 极具 性价比 豪华 豪华车 配置 空间 动力 输 德 系 日 系 豪 车 发动 发动机 动机 更是 年 全球 十佳 发动 发动机 动机 称号 即日 即日起 起到 月 日 购买 飞 思 享 元 现金 优惠 感兴 感兴趣 兴趣 朋友 电 经销 经销商 店 咨询 文 汽车 点评 网 易 丽 君\n'

In [20]:
countVectorizer = CountVectorizer(
    stop_words=stopwords, #前面获取到的stopwords列表, 
    #CountVectorizer可以在建模时直接过滤停用词，但build_corpus为了兼容生成可供gensim使用的语料，在该函数内过滤停用词
    min_df=0, token_pattern=r"\b\w+\b"
)
print(datetime.now())
textVector = countVectorizer.fit_transform(
    space_seperated_list
)
print(datetime.now())

2018-04-29 21:23:16.074825
2018-04-29 21:23:25.652295


In [17]:
from sklearn.metrics import pairwise_distances

print(datetime.now())
distance_matrix = pairwise_distances(
    textVector, 
    metric="cosine"
)
print(datetime.now())

2018-04-29 17:44:51.902724
2018-04-29 18:05:20.692795


三万篇文章两两计算余弦距离耗时3分钟
四万篇文章两两计算余弦距离耗时5分钟
五万篇文章两两计算余弦距离耗时21分钟  
存在计算完成后内存未释放的问题

In [19]:
type(distance_matrix)

numpy.ndarray

In [25]:
similarity_matrix = pd.DataFrame(1 - distance_matrix)

In [28]:
import numpy as np
print(datetime.now())
sort = np.argsort(distance_matrix, axis=1)[:, 1:] #排序后第一个是文档自身
print(datetime.now())

2018-04-29 19:05:12.442418
2018-04-29 19:11:00.338987


耗时6分钟

In [32]:
sort[0]

array([ 1861,  3883,  3382, ..., 30397, 30421, 24999], dtype=int64)

两两计算距离太耗时并且不能实时反应最新文档库的数据  
尝试仅针对查询目标文档计算距离

fit CountVectorizer模型的时候必须基于完整语料，否则不同文档的文本向量对应位置词不同，无法比较

In [46]:
textVector

<50000x155213 sparse matrix of type '<class 'numpy.int64'>'
	with 7432101 stored elements in Compressed Sparse Row format>

In [30]:
type(textVector)

scipy.sparse.csr.csr_matrix

In [32]:
textVector.get_shape()

(50000, 155213)

In [22]:
# 使用上面构造好的textVector matrix
textVector.toarray() #Memory Error
textVector[0].toarray()

array([[0, 0, 0, ..., 0, 0, 0]], dtype=int64)

In [24]:
len(textVector[0].toarray()[0]) # 155213个词

155213

In [26]:
textVector[:2].toarray()

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=int64)

In [27]:
# refer to cosine() function in scipy.spatial.distance
def cosine_distance(arr1, arr2):
    distance = 1 - np.dot(arr1,arr2) / (norm(arr1) * norm(arr2))
    return distance

In [47]:
from scipy.spatial import distance as scidis
# 假设要查找第一个文档的相似文档
#query_doc = space_seperated_list[0]
query_vec = textVector[0].toarray()

print(datetime.now())
#df_textVector = pd.DataFrame(textVector.toarray())#Memory Error
distances = []
for i in range(textVector.get_shape()[0]):
    #distance = cosine_distance(query_vec,textVector[i])
    distance = scidis.cosine(query_vec,textVector[i].toarray())
    distances.append(distance)
print(datetime.now())

2018-04-29 22:15:03.073372


C:\ProgramData\Anaconda3\lib\site-packages\scipy\spatial\distance.py:505: RuntimeWarning: invalid value encountered in true_divide
  dist = 1.0 - np.dot(u, v) / (norm(u) * norm(v))


2018-04-29 22:17:57.503461


计算被查询文档和其他所有文档的距离，50000篇文章的计算量仍需要3分钟左右

In [53]:
np.argsort(np.array(distances))[1:]

array([ 1861,  3883,  3382, ..., 30569, 30731,  1000], dtype=int64)

# 构造gensim需要的语料
使用gensim实现, 需要的语料是list of list

In [1]:
import jieba
from datetime import datetime

In [54]:
filename = 'words_comma_separated_list.txt'

if os.path.exists(filename):
    os.remove(filename)
    
print(datetime.now())
df_news.content.apply(build_corpus,args=(True,filename,','))
print(datetime.now())

2018-04-30 06:34:33.511948
2018-04-30 06:37:50.633219


In [2]:
#从文件中读取list of list
def read_list_of_list(file):
    word_list_of_list = []
    with open(file,'r') as f:
        for line in f.readlines():
            word_list = line.split(',')
            word_list_of_list.append(word_list)
    return word_list_of_list   

In [5]:
contents_list_of_list = read_corpus(r'words_comma_seperated_list.txt','listoflist',',')
contents_list_of_list

[['近日',
  '编辑',
  '进口',
  '合肥',
  '肥地',
  '地区',
  '经销',
  '经销商',
  '处',
  '即日',
  '即日起',
  '起至',
  '月',
  '日',
  '该店',
  '购买',
  '飞',
  '思',
  '现金',
  '直',
  '降',
  '元',
  '店',
  '现',
  '车',
  '充足',
  '颜色',
  '齐全',
  '更多',
  '详情',
  '详情请',
  '咨询',
  '经销',
  '经销商',
  '飞',
  '思',
  '车型',
  '最新',
  '价格',
  '表',
  '伤',
  '汲',
  '敌',
  '妥',
  '钚',
  '录',
  '鄹',
  '癖',
  '浠',
  '表',
  '邢',
  '殖',
  '担',
  '颜色',
  '全',
  '更多',
  '详情',
  '详情请',
  '咨询',
  '经销',
  '经销商',
  '雅科',
  '仕',
  '车型',
  '配置',
  '图片',
  '报价',
  '质保',
  '周期',
  '五年',
  '公里',
  '店',
  '内建',
  '建议',
  '保养',
  '周期',
  '万公里',
  '公里',
  '更换',
  '机油',
  '油机',
  '机滤',
  '费用',
  '元',
  '更换',
  '机油',
  '三滤',
  '费用',
  '元',
  '保养',
  '信息',
  '当天',
  '店',
  '保养',
  '信息',
  '为准',
  '嗉',
  '点评',
  '口',
  '雅科',
  '仕',
  '一款',
  '极具',
  '性价比',
  '豪华',
  '豪华车',
  '配置',
  '空间',
  '动力',
  '输',
  '德',
  '系',
  '日',
  '系',
  '豪',
  '车',
  '发动',
  '发动机',
  '动机',
  '更是',
  '年',
  '全球',
  '十佳',
  '发动',
  '发动机',
  '动机',
  '称号',
  '即日',
  '即日起',


# 查找相似文章的实现步骤

1. 基于语料里的全部文档抽取一个“词袋（bag-of-words)"，结果如下：  
{'一款': 0, '万公里': 1, '三滤': 2, '为准': 3, '丽': 4, '五年': 5, '享': 6, '仕': 7, '价格': 8, '优惠': 9, '伤': 10,...}  
2. 将用字符串表示的文档转换为用id表示的文档向量,结果如下：  
[[(0, 1),  (1, 1),  (2, 1),  (3, 1),  (4, 1),  (5, 1),  (6, 1),  (7, 2),  (8, 1),  (9, 1),  (10, 1),...],  
[(10, 1),  (21, 3),  (25, 3),  (26, 3),  (33, 3),  (37, 5),  (38, 5),  (47, 3),  (48, 1),  (53, 2),  (54, 2),...],  
...  
]]  
例如(0, 1)代表id为0的词在当前文档中出现了1次  
3. 基于这些“训练文档”计算一个TF-IDF“模型”。  
参考文档:  
TF-IDF与余弦相似性的应用（一）：自动提取关键词: http://www.ruanyifeng.com/blog/2013/03/tf-idf.html  
TF-IDF与余弦相似性的应用（二）：找出相似文章： http://www.ruanyifeng.com/blog/2013/03/cosine_similarity.html
4. 基于这个TF-IDF模型，将上述用词频表示文档向量表示为一个用tf-idf值表示的文档向量  
5. 训练一个LSI模型  
参考文档:  
(译)隐含语义索引——快速教程(Latent Semantic Indexing(LSI)---A Fast Track Turorial)https://blog.csdn.net/a123456ei/article/details/22801967  
6. 构造相似度矩阵  
7. 通过lsi模型将选定的文档映射到10个topic主题模型空间上，然后和其他文档计算相似度  

  
下面一步步实现

In [6]:
from gensim import corpora, models, similarities
#import logging #print_debug会输出到Log
#logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)


C:\ProgramData\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")


In [7]:
print(datetime.now())
dictionary = corpora.Dictionary(contents_list_of_list)
dictionary.token2id
print(datetime.now())

2018-04-30 11:15:47.870369
2018-04-30 11:16:06.398286


In [22]:
len(list(dictionary.token2id.keys())) # 167705个词

167705

将用字符串表示的文档转换为用id表示的文档向量

In [8]:
print(datetime.now())
corpus = [dictionary.doc2bow(content) for content in contents_list_of_list]
print(datetime.now())
corpus[:5]

2018-04-30 11:16:06.406840
2018-04-30 11:16:20.675381


[[(0, 1),
  (1, 1),
  (2, 1),
  (3, 1),
  (4, 1),
  (5, 1),
  (6, 1),
  (7, 2),
  (8, 1),
  (9, 1),
  (10, 1),
  (11, 3),
  (12, 2),
  (13, 4),
  (14, 1),
  (15, 1),
  (16, 1),
  (17, 2),
  (18, 1),
  (19, 1),
  (20, 1),
  (21, 2),
  (22, 1),
  (23, 2),
  (24, 2),
  (25, 2),
  (26, 2),
  (27, 1),
  (28, 1),
  (29, 1),
  (30, 2),
  (31, 3),
  (32, 1),
  (33, 1),
  (34, 1),
  (35, 1),
  (36, 1),
  (37, 1),
  (38, 4),
  (39, 1),
  (40, 1),
  (41, 1),
  (42, 1),
  (43, 3),
  (44, 1),
  (45, 1),
  (46, 1),
  (47, 1),
  (48, 1),
  (49, 1),
  (50, 1),
  (51, 3),
  (52, 1),
  (53, 2),
  (54, 2),
  (55, 1),
  (56, 1),
  (57, 2),
  (58, 1),
  (59, 2),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 1),
  (64, 1),
  (65, 1),
  (66, 1),
  (67, 2),
  (68, 1),
  (69, 2),
  (70, 1),
  (71, 1),
  (72, 1),
  (73, 1),
  (74, 1),
  (75, 2),
  (76, 4),
  (77, 4),
  (78, 1),
  (79, 1),
  (80, 1),
  (81, 2),
  (82, 1),
  (83, 2),
  (84, 2),
  (85, 1),
  (86, 1),
  (87, 1),
  (88, 1),
  (89, 2),
  (90, 2),
  (91, 1)

例如corpus[0]中的(0,1)表示‘一款’这个词在第一篇文章（corpus[0]）中出现了1次  
现在基于这些“训练文档”计算一个TF-IDF“模型”

In [9]:
print(datetime.now())
tfidf = models.TfidfModel(corpus) # fit model
print(datetime.now())

2018-04-30 11:16:20.717494
2018-04-30 11:16:24.906339


In [16]:
tfidf.__getitem__(corpus[0])

[(0, 0.048201488659442751),
 (1, 0.078526002388932648),
 (2, 0.090826618106530629),
 (3, 0.07833557271955402),
 (4, 0.062184950039278229),
 (5, 0.066941610884753894),
 (6, 0.073956745004550226),
 (7, 0.16130989646821231),
 (8, 0.037091984795780283),
 (9, 0.051768365796229975),
 (10, 0.060796503529436587),
 (11, 0.19143778325678074),
 (12, 0.074497898649837899),
 (13, 0.15459168206555407),
 (14, 0.063905977189115823),
 (15, 0.045033924906410443),
 (16, 0.041937947306250868),
 (17, 0.099653887176990877),
 (18, 0.050698969502841973),
 (19, 0.10352081216765305),
 (20, 0.044982720416906853),
 (21, 0.093623186559428542),
 (22, 0.098978911903545935),
 (23, 0.17649026860485142),
 (24, 0.17936694023072103),
 (25, 0.090494133502147314),
 (26, 0.096998746630895694),
 (27, 0.067380870161099476),
 (28, 0.089276904315835001),
 (29, 0.10668293456975857),
 (30, 0.12058888245772785),
 (31, 0.16028111612306345),
 (32, 0.050270203770811393),
 (33, 0.046986494777535769),
 (34, 0.0392733106354754),
 (35, 0

In [13]:
tfidf[corpus[0]]

[(0, 0.048201488659442751),
 (1, 0.078526002388932648),
 (2, 0.090826618106530629),
 (3, 0.07833557271955402),
 (4, 0.062184950039278229),
 (5, 0.066941610884753894),
 (6, 0.073956745004550226),
 (7, 0.16130989646821231),
 (8, 0.037091984795780283),
 (9, 0.051768365796229975),
 (10, 0.060796503529436587),
 (11, 0.19143778325678074),
 (12, 0.074497898649837899),
 (13, 0.15459168206555407),
 (14, 0.063905977189115823),
 (15, 0.045033924906410443),
 (16, 0.041937947306250868),
 (17, 0.099653887176990877),
 (18, 0.050698969502841973),
 (19, 0.10352081216765305),
 (20, 0.044982720416906853),
 (21, 0.093623186559428542),
 (22, 0.098978911903545935),
 (23, 0.17649026860485142),
 (24, 0.17936694023072103),
 (25, 0.090494133502147314),
 (26, 0.096998746630895694),
 (27, 0.067380870161099476),
 (28, 0.089276904315835001),
 (29, 0.10668293456975857),
 (30, 0.12058888245772785),
 (31, 0.16028111612306345),
 (32, 0.050270203770811393),
 (33, 0.046986494777535769),
 (34, 0.0392733106354754),
 (35, 0

基于这个TF-IDF模型，将上述用词频表示文档向量表示为一个用tf-idf值表示的文档向量

In [10]:
corpus_tfidf = tfidf[corpus] # apply model
corpus_tfidf[0]

[(0, 0.048201488659442751),
 (1, 0.078526002388932648),
 (2, 0.090826618106530629),
 (3, 0.07833557271955402),
 (4, 0.062184950039278229),
 (5, 0.066941610884753894),
 (6, 0.073956745004550226),
 (7, 0.16130989646821231),
 (8, 0.037091984795780283),
 (9, 0.051768365796229975),
 (10, 0.060796503529436587),
 (11, 0.19143778325678074),
 (12, 0.074497898649837899),
 (13, 0.15459168206555407),
 (14, 0.063905977189115823),
 (15, 0.045033924906410443),
 (16, 0.041937947306250868),
 (17, 0.099653887176990877),
 (18, 0.050698969502841973),
 (19, 0.10352081216765305),
 (20, 0.044982720416906853),
 (21, 0.093623186559428542),
 (22, 0.098978911903545935),
 (23, 0.17649026860485142),
 (24, 0.17936694023072103),
 (25, 0.090494133502147314),
 (26, 0.096998746630895694),
 (27, 0.067380870161099476),
 (28, 0.089276904315835001),
 (29, 0.10668293456975857),
 (30, 0.12058888245772785),
 (31, 0.16028111612306345),
 (32, 0.050270203770811393),
 (33, 0.046986494777535769),
 (34, 0.0392733106354754),
 (35, 0

有了tf-idf值表示的文档向量，我们就可以训练一个LSI模型. 这里姑且确定LSI模型的topic数量为10。
num_topics (int, optional) – Number of requested factors (latent dimensions)
类似PCA降维中的K值？K<=number of documents？
LSI:  
我们考察两个词的关系常常考虑的是它们在一个窗口长度（譬如一句话，一段话或一个文章）里的共现情况，在语料库语言学里有个专业点叫法叫Collocation，中文译为搭配或词语搭配。而LSI所做的是挖掘如下这层词语关系：A和C共现，B和C共现，目标是找到A和B的隐含关系，学术一点的叫法是second-order co-ocurrence。

In [11]:
print(datetime.now())
lsi = models.LsiModel(corpus_tfidf, id2word=dictionary, num_topics=10)
print(datetime.now())

2018-04-30 11:16:37.467084
2018-04-30 11:18:04.505733


In [83]:
lsi.print_topics()
#Get the most significant topics (alias for show_topics() method).

2018-04-30 07:41:10,134 : INFO : topic #0(18.594): 0.150*"车型" + 0.126*"市场" + 0.124*"中国" + 0.113*"公司" + 0.108*"汽车" + 0.084*"投资" + 0.080*"年" + 0.077*"埃" + 0.076*"月" + 0.075*"经济"
2018-04-30 07:41:10,148 : INFO : topic #1(13.365): 0.412*"车型" + 0.172*"发动机" + 0.169*"动机" + 0.168*"发动" + 0.138*"款" + 0.127*"报价" + 0.121*"车" + 0.118*"汽车" + 0.117*"配置" + 0.108*"设计"
2018-04-30 07:41:10,163 : INFO : topic #2(12.387): -0.197*"银行" + -0.190*"基金" + -0.179*"投资" + -0.166*"市场" + -0.137*"公司" + 0.129*"比赛" + -0.126*"利率" + 0.126*"奥运" + -0.119*"增长" + -0.119*"经济"
2018-04-30 07:41:10,173 : INFO : topic #3(12.067): -0.489*"网校
" + -0.481*"北京四中" + -0.464*"四中" + -0.422*"中网" + -0.277*"来源" + -0.150*"北京" + -0.032*"银行" + -0.030*"基金" + 0.030*"车型" + 0.030*"比赛"
2018-04-30 07:41:10,188 : INFO : topic #4(11.917): 0.279*"考生" + 0.246*"录取" + 0.225*"志愿" + -0.192*"比赛" + 0.190*"高考" + -0.190*"奥运" + 0.161*"学校" + 0.157*"教育" + 0.152*"招生" + 0.151*"学生"
2018-04-30 07:41:10,205 : INFO : topic #5(11.174): -0.348*"无人机" + -0.332*"人机" + -0.281*"

[(0,
  '0.150*"车型" + 0.126*"市场" + 0.124*"中国" + 0.113*"公司" + 0.108*"汽车" + 0.084*"投资" + 0.080*"年" + 0.077*"埃" + 0.076*"月" + 0.075*"经济"'),
 (1,
  '0.412*"车型" + 0.172*"发动机" + 0.169*"动机" + 0.168*"发动" + 0.138*"款" + 0.127*"报价" + 0.121*"车" + 0.118*"汽车" + 0.117*"配置" + 0.108*"设计"'),
 (2,
  '-0.197*"银行" + -0.190*"基金" + -0.179*"投资" + -0.166*"市场" + -0.137*"公司" + 0.129*"比赛" + -0.126*"利率" + 0.126*"奥运" + -0.119*"增长" + -0.119*"经济"'),
 (3,
  '-0.489*"网校\n" + -0.481*"北京四中" + -0.464*"四中" + -0.422*"中网" + -0.277*"来源" + -0.150*"北京" + -0.032*"银行" + -0.030*"基金" + 0.030*"车型" + 0.030*"比赛"'),
 (4,
  '0.279*"考生" + 0.246*"录取" + 0.225*"志愿" + -0.192*"比赛" + 0.190*"高考" + -0.190*"奥运" + 0.161*"学校" + 0.157*"教育" + 0.152*"招生" + 0.151*"学生"'),
 (5,
  '-0.348*"无人机" + -0.332*"人机" + -0.281*"无人" + -0.249*"懂得" + -0.232*"战争" + -0.215*"发动战争" + -0.174*"天空" + -0.168*"海洋" + -0.156*"发动" + -0.142*"日本"'),
 (6,
  '-0.413*"转" + -0.338*"埃" + -0.323*"号" + -0.304*"福" + -0.268*"矗" + -0.164*"汽车" + -0.138*"路" + -0.136*"保" + 0.129*"车型" + -0.123*"车

In [74]:
lsi.print_debug() #print to log
Unlike print_topics(), this looks for words that are significant for a particular topic and not for others. This should result in a more human-interpretable description of topics.

2018-04-30 07:21:59,446 : INFO : computing word-topic salience for 20 topics
2018-04-30 07:22:06,298 : INFO : topic #0(18.725): 之外(0.013), 中(0.069), 外(0.021), 很大(0.018), 送(0.020), 壳(0.014), 杂(0.014), 三个(0.013), 氖(0.014), 正(0.018), ..., 
(-0.000)
2018-04-30 07:22:06,543 : INFO : topic #1(13.452): 轴距(0.041), 紧凑型(0.012), 一款(0.054), 底盘(0.014), 外观(0.058), 紧凑(0.024), 运动版(0.007), 该车(0.037), 车身(0.067), 同级(0.024), ..., 参加(-0.033), 希望(-0.023), 罢(-0.004), 崾(-0.004), 最终(-0.017)
2018-04-30 07:22:06,794 : INFO : topic #2(12.559): 大幅(-0.031), 期内(-0.011), 低于(-0.018), 策略(-0.015), 赋(-0.006), 季末(-0.005), 持续(-0.028), 证券报(-0.003), 耸(-0.011), 活跃度(-0.002), ..., 感觉(0.021), 出色(0.017), 顶(0.005), 浅(0.005), 拥(0.006)
2018-04-30 07:22:07,057 : INFO : topic #3(12.072): 北京四中(-0.483), 四中(-0.467), 网校
(-0.492), 中网(-0.425), 来源(-0.278), 北京(-0.153), 安生(-0.000), 特训营(-0.000), 人民网
(-0.000), 纪念版
(-0.000), ..., 赛前(0.004), 出色(0.004), 对阵(0.004), 窘(0.001), 险些(0.000)
2018-04-30 07:22:07,320 : INFO : topic #4(11.969): 咨询会(0.008), 全省

In [84]:
print(lsi.get_topics().shape)
lsi.get_topics()

(10, 167705)


array([[  2.79751871e-02,   5.55460175e-03,   3.09235890e-03, ...,
          8.37102654e-06,   3.94580795e-05,   1.66172746e-05],
       [  5.48598964e-02,   1.11305861e-02,   7.46124536e-03, ...,
         -7.73001158e-06,  -1.06209849e-05,  -4.77382582e-06],
       [  1.04581282e-02,   2.87172981e-03,   1.91547598e-03, ...,
          8.07377972e-06,   3.20149055e-05,   1.34905337e-05],
       ..., 
       [  9.05710578e-03,  -1.45451712e-03,  -2.15742951e-03, ...,
          1.18416512e-05,   5.14761358e-05,   1.93855718e-05],
       [  1.11052523e-02,  -3.02644067e-03,  -2.25085454e-03, ...,
         -1.51544592e-05,  -4.23313039e-05,  -1.36026717e-05],
       [  7.78301816e-04,   6.86606448e-05,   7.51220209e-05, ...,
          4.88249933e-06,   1.61638068e-05,   1.24356083e-06]])

In [13]:
print(corpus[0])
print(lsi[corpus[0]])

[(0, 1), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 2), (8, 1), (9, 1), (10, 1), (11, 3), (12, 2), (13, 4), (14, 1), (15, 1), (16, 1), (17, 2), (18, 1), (19, 1), (20, 1), (21, 2), (22, 1), (23, 2), (24, 2), (25, 2), (26, 2), (27, 1), (28, 1), (29, 1), (30, 2), (31, 3), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 1), (38, 4), (39, 1), (40, 1), (41, 1), (42, 1), (43, 3), (44, 1), (45, 1), (46, 1), (47, 1), (48, 1), (49, 1), (50, 1), (51, 3), (52, 1), (53, 2), (54, 2), (55, 1), (56, 1), (57, 2), (58, 1), (59, 2), (60, 1), (61, 1), (62, 1), (63, 1), (64, 1), (65, 1), (66, 1), (67, 2), (68, 1), (69, 2), (70, 1), (71, 1), (72, 1), (73, 1), (74, 1), (75, 2), (76, 4), (77, 4), (78, 1), (79, 1), (80, 1), (81, 2), (82, 1), (83, 2), (84, 2), (85, 1), (86, 1), (87, 1), (88, 1), (89, 2), (90, 2), (91, 1), (92, 1), (93, 2), (94, 2), (95, 1), (96, 1), (97, 1), (98, 1), (99, 1), (100, 2), (101, 1), (102, 1), (103, 2), (104, 2), (105, 3), (106, 1)]
[(0, 4.0369995273969908), (1, 5.0311326

In [90]:
print(corpus_tfidf[0][:10])
lsi[corpus_tfidf[0]]

[(0, 0.048201488659442751), (1, 0.078526002388932648), (2, 0.090826618106530629), (3, 0.07833557271955402), (4, 0.062184950039278229), (5, 0.066941610884753894), (6, 0.073956745004550226), (7, 0.16130989646821231), (8, 0.037091984795780283), (9, 0.051768365796229975)]


[(0, 0.18226160126040519),
 (1, 0.25689793446570675),
 (2, 0.062005735575345007),
 (3, 0.020522020766139248),
 (4, 0.035008268951321718),
 (5, 0.017923185257697628),
 (6, 0.011317268361112324),
 (7, -0.040292398528473418),
 (8, -0.02974344485929337),
 (9, -0.0061946542333882332)]

文档0和topic[1]最相关

# 使用原始的corpus构造相似度矩阵  
因gensim官方文档中MatrixSimilarity的参数corpus是 Corpus in BoW format， 首先尝试使用原始的corpus构造相似度矩阵(不考虑LSI模型)

In [57]:
print(datetime.now())
index_corpus = similarities.MatrixSimilarity(corpus) #3 minutes
#dict_size = len(list(dictionary.token2id.keys()))
#index = similarities.MatrixSimilarity(corpus,num_features = dict_size)
print(datetime.now())

2018-04-30 16:12:41.022141
2018-04-30 16:16:05.435636


In [58]:
#随机取一篇文章来测试
document = contents_list_of_list[29981]
bow = dictionary.doc2bow(document) #bow = corpus[29981]
#doc_lsi = lsi[bow]

In [61]:
bow[:10]

[(37, 10),
 (108, 1),
 (174, 1),
 (517, 2),
 (663, 1),
 (803, 1),
 (960, 2),
 (1261, 1),
 (1284, 1),
 (1304, 1)]

In [62]:
print(datetime.now())
#sims = index[doc_lsi] # index: similarities.MatrixSimilarity
sims = index_corpus[bow] 
sort_sims = sorted(enumerate(sims), key=lambda item: -item[1])
print(datetime.now())
sort_sims[:10]

2018-04-30 16:18:26.273044
2018-04-30 16:20:01.154099


[(29981, 1.0),
 (27510, 0.82222021),
 (26013, 0.82215959),
 (28295, 0.48575795),
 (27248, 0.48520058),
 (33326, 0.36477154),
 (697, 0.30130327),
 (41197, 0.29967132),
 (821, 0.29827499),
 (45593, 0.29827499)]

In [63]:
for i in [s[0] for s in sort_sims[:10]]:
    print(df_news.iloc[i]['content'])
    print("---------------------------")

从２００４年至２０１１年，北京高考文理科第一名共有１９人。其中，文科第一名１０人，理科第一名９人。３鱿植⒘忻次的年份共有２年：分别为２００５年和２０１１年。其中２００５年为２位理科头名并列；２０１１年为３位文科头名并列。０凑招员鸹分，第一名呈现阴盛阳衰之势；女性第一名占了绝大多数，共有１４位；除了２００４年第一名全部为男生外，其余年份均有女生；其中还有４年文理头名皆为女生，没有男生。４油访们来自的中学看，共有８位头名来自人大附中（含人大附中分校），其中文科２人，理科６人，除２００６年没有产生文理第一名外，其余年份，人大附中每年都会毫无悬念地产生至少一位头名。３了人大附中外，还有８所学校产生过文理科第一名，这些学校分别位于海淀、西城和东城。４油访们最终选择的高校看，８年来，香港高校与北大、清华争夺高考第一名的激烈程度已进入白热化，１１名头名最终选择在香港高校就读。
---------------------------
从２００４年至２０１１年，北京高考文理科第一名共有１９人。其中，文科第一名１０人，理科第一名９人。３鱿植⒘忻次的年份共有２年：分别为２００５年和２０１１年。其中２００５年为２位理科头名并列﹔２０１１年为３位文科头名并列。０凑招员鸹分，第一名呈现阴盛阳衰之势﹔女性第一名占了绝大多数，共有１４位﹔除了２００４年第一名全部为男生外，其余年份均有女生﹔其中还有４年文理头名皆为女生，没有男生。４油访们来自的中学看，共有８位头名来自人大附中（含人大附中分校），其中文科２人，理科６人，除２００６年没有产生文理第一名外，其余年份，人大附中每年都会毫无悬念地产生至少一位头名。３了人大附中外，还有８所学校产生过文理科第一名，这些学校分别位於海淀、西城和东城。４油访们最终选择的高校看，８年来，香港高校与北大、清华争夺高考第一名的激烈程度已进入白热化，１１名头名最终选择在香港高校就读。９鄄忑８呖纪访背后的“冷热不均”！澳惚考了港校吗？”这已经成为每年采访北京高考第一名的必问问题。＃玻埃埃的辏来自人大附中的理科第一名陈秀野，意外地选择了香港科技大学生化专业就读，而放弃了此前报考的清华大学生物专业，成为近年来“弃清华选港校”的第一人。８呖嫉谝幻的选择，无疑对香港高校产生了巨大的宣传效应。尽管２０００年前后，个别香港高校就已进入内地招生，但港校真正进入大多数人的视野，还要归功於高考

前面几个结果还可以，后面几个不匹配

In [69]:
#构造一篇新文章
document = "广东省纪委于4月27日通报了一则消息：中山市委原副秘书长邓洁（正处级）涉嫌严重违纪违法，目前正在接受纪律审查和监察调查"
content = build_corpus(document,False,delimiter = ',')
print(content)

bow_doc = dictionary.doc2bow(content) 
#通过lsi模型将选定的文档映射到10个topic主题模型空间上
#doc_lsi = lsi[bow]

['广东', '广东省', '省纪委', '纪委', '月', '27', '日', '通报', '消息', '中山', '中山市', '市委', '原', '副', '秘书', '秘书长', '邓', '洁', '正处', '正处级', '处级', '涉嫌', '违纪', '违法', '接受', '纪律', '审查', '监察', '调查']


In [70]:
print(datetime.now())
sims = index_corpus[bow_doc] 
print(datetime.now())

2018-04-30 16:28:34.373971
2018-04-30 16:30:17.781428


In [72]:
sort_sims = sorted(enumerate(sims), key=lambda item: -item[1])
sort_sims[:10]

[(27491, 0.2373068),
 (27806, 0.23724687),
 (27256, 0.20847419),
 (27056, 0.20770964),
 (6813, 0.20693451),
 (8306, 0.20490028),
 (4205, 0.20106746),
 (26314, 0.19804005),
 (27801, 0.19205531),
 (28811, 0.19205531)]

In [73]:
for i in [s[0] for s in sort_sims[:10]]:
    print(df_news.iloc[i]['content'])
    print("---------------------------")

６月２１日晚，广西壮族自治区招生考试委员会召开全体委员会议，确定广西壮族自治区２０１２年普通高校招生录取工作将于７月４日正式开始，至８月１９日结束。Ｄ壳埃考生志愿填报工作正有条不紊地进行着，广西壮族自治区录取工作具体时间安排如下：１究铺崆芭：７月４日－７月９日，其中体育、艺术类征集志愿（艺术类只征集使用广西艺术统考成绩的专业）时间：７月８日１２∶００开始；６懒⒀г罕究铺崆芭（含艺术类专业和体育类专业）：７月９日－７月１２日，其中征集志愿时间：７月１１日１７∶００开始；Ｆ独У厍专项计划：７月９日－７月１２日，其中征集志愿时间：７月１０日１７∶００开始；Ｗ灾餮“温既∨：７月１２日１１∶００－７月１３日１１∶００；１究频谝慌Ａ类：７月１２日－７月１６日，其中征集志愿时间：７月１５日１７∶００开始；１究频谝慌Ｂ类（含本科第一批预科和学校申请安排在Ｂ类的专业）７月１６日－７月１８日，其中征集志愿时间：７月１７日１７∶００开始；１究频诙批：７月１９日－７月２５日，其中征集志愿时间：７月２３日１６∶００开始；１究频诙批预科批Ａ类（区内免费预科生）：７月２５日－７月２６日；１究频诙批预科批Ｂ类（含区内普通民族预科班和区外本科第二批预科）：７月２７日；１究频谌批（独立学院）：７月２８日－７月３１日，其中征集志愿时间：７月３０日１６∶００开始；１究频谌批（独立学院）预科：８月１日；？忌填报高职高专其他批次志愿：８月２日－８月７日；８咧案咦ㄌ崆芭：８月７日－８月１２日，其中征集志愿时间：８月１０日１６∶００开始；８咧案咦ㄆ胀ㄅ：８月１２日－８月１８日，其中征集志愿时间：８月１５日１６∶００开始；８咧案咦ㄔた婆：８月１８日－８月１９日。
---------------------------
６月２１日晚，广西壮族自治区招生考试委员会召开全体委员会议，确定广西壮族自治区２０１２年普通高校招生录取工作将於７月４日正式开始，至８月１９日结束。Ｄ壳埃考生志愿填报工作正有条不紊地进行著，广西壮族自治区录取工作具体时间安排如下：１究铺崆芭：７月４日－７月９日，其中体育、艺术类征集志愿（艺术类只征集使用广西艺术统考成绩的专业）时间：７月８日１２︰００开始﹔６懒⒀г罕究铺崆芭（含艺术类专业和体育类专业）：７月９日－７月１２日，其中征集志愿时间：７月１１日１７︰００开始﹔Ｆ独У厍专项计划：７月９日－７月１

完全不搭界

# 使用原始corpus的LSI模型来构造相似度矩阵
构造相似度矩阵,参考资料中这一步是用lsi[corpus]来建索引的，但为何不是lsi[corpus_tfidf]?

In [44]:
print(datetime.now())
index = similarities.MatrixSimilarity(lsi[corpus]) # 12 seconds
#dict_size = len(list(dictionary.token2id.keys()))
#index = similarities.MatrixSimilarity(lsi[corpus],num_features = dict_size)
print(datetime.now())

2018-04-30 15:55:31.163244
2018-04-30 15:55:42.690001


num_features (int, optional) – Size of the dictionary.
添加num_features参数耗时3分钟，不添加num_features参数报WARNING : scanning corpus to determine the number of features (consider setting `num_features` explicitly),反而只需要12秒（50000篇文档）

通过lsi模型将选定的文档映射到10个topic主题模型空间上，然后和其他文档计算相似度

In [45]:
#随机取一篇文章来测试
document = contents_list_of_list[29981]
bow = dictionary.doc2bow(document) #bow = corpus[29981]
doc_lsi = lsi[bow]

In [34]:
doc_lsi

[(0, 2.2153423317337149),
 (1, -1.5725031833981973),
 (2, 1.1097049704804429),
 (3, 0.053894998996866027),
 (4, 1.6667977546567128),
 (5, 0.22825720196925295),
 (6, 0.64222753574178171),
 (7, -0.65436013493785594),
 (8, 0.3071507443892218),
 (9, -0.1030159220238121)]

可以看到这篇文章和topic[0]最相关

In [35]:
lsi[corpus[29981]]

[(0, 2.2153423317337149),
 (1, -1.5725031833981973),
 (2, 1.1097049704804429),
 (3, 0.053894998996866027),
 (4, 1.6667977546567128),
 (5, 0.22825720196925295),
 (6, 0.64222753574178171),
 (7, -0.65436013493785594),
 (8, 0.3071507443892218),
 (9, -0.1030159220238121)]

In [36]:
print(datetime.now())
sims = index[doc_lsi] # index: similarities.MatrixSimilarity
sort_sims = sorted(enumerate(sims), key=lambda item: -item[1])
print(datetime.now())
sort_sims[:10]

2018-04-30 15:35:15.114372
2018-04-30 15:35:15.192579


[(29981, 1.0),
 (27401, 0.99265188),
 (29662, 0.99193752),
 (27057, 0.98975587),
 (25198, 0.98907667),
 (27407, 0.98863447),
 (26403, 0.9881196),
 (25867, 0.98768234),
 (27911, 0.98670095),
 (26170, 0.98667222)]

In [37]:
for i in [s[0] for s in sort_sims[:10]]:
    print(df_news.iloc[i]['content'])
    print("---------------------------")

从２００４年至２０１１年，北京高考文理科第一名共有１９人。其中，文科第一名１０人，理科第一名９人。３鱿植⒘忻次的年份共有２年：分别为２００５年和２０１１年。其中２００５年为２位理科头名并列；２０１１年为３位文科头名并列。０凑招员鸹分，第一名呈现阴盛阳衰之势；女性第一名占了绝大多数，共有１４位；除了２００４年第一名全部为男生外，其余年份均有女生；其中还有４年文理头名皆为女生，没有男生。４油访们来自的中学看，共有８位头名来自人大附中（含人大附中分校），其中文科２人，理科６人，除２００６年没有产生文理第一名外，其余年份，人大附中每年都会毫无悬念地产生至少一位头名。３了人大附中外，还有８所学校产生过文理科第一名，这些学校分别位于海淀、西城和东城。４油访们最终选择的高校看，８年来，香港高校与北大、清华争夺高考第一名的激烈程度已进入白热化，１１名头名最终选择在香港高校就读。
---------------------------
中考取得高分的双胞胎兄弟。Ｗ蛱欤广州市招考办公布　２０１２年广州市中考分数段统计表　。在计算了政策性加分后，全市共有４１９名考生总分在７５０分以上。提前批上线考生数和提前批学位比为１．２５，相当于５个上线考生争４个学位。另外，全市共有７．７万名中考生超过了普通高中最低录取控制线。Ｊ∈邓胞胎兄弟齐齐获高分＝衲曛锌嫉母叻盅生中，省实的一对双胞胎兄弟特别引人注目。他们除了长相神似之外，分数也不相上下。“他们初中三年总分相差一般不会超过５分，我都怀疑他们是不是有心灵感应了！”他们的年级长笑着告诉记者。而在中考中，两兄弟一个考了７５７分，另一个考了７６３分。３錾于军人家庭的两兄弟，从小接受相对严格的家庭教育，从而培养了较强的自律意识。尤其是哥哥冠尧，自称忧患意识比较强烈。“看到一些神童，年纪这么小就那么优秀，让我很惭愧。”而弟弟冠杰则相对活泼一些，整个采访过程说话的频率明显比哥哥高。他还打趣地评价哥哥，“他就是比较传统。他基本不会接触娱乐、八卦类的东西。”“他几乎不用ＱＱ。”弟弟冠杰还向记者“爆料”。哥哥冠尧解释道：“有，但不怎么用，一年就上几次。”记者问冠杰是不是经常玩ＱＱ，没想到冠杰却故作深沉地说：“我不是在玩ＱＱ，是在用ＱＱ。”一句话逗乐了在场所有人。Ａ叫值艽有〉酱蠖荚谝桓霭喽潦椋从未分开。因此，两个人除了生活上是兄弟外，学习上也是不离不弃的“战友”。以至

In [117]:
#构造一篇新文章
document = "根据“电影票房”给出的证据，刘若英的导演处女作《后来的我们》预售票房极佳，但有人利用票务平台可以退票的规则便利，在影片开映前恶意退票，仅武汉万达的几家影城就累计退票4342张。"
content = build_corpus(document,False,delimiter = ',')
print(content)

bow = dictionary.doc2bow(content) 
#通过lsi模型将选定的文档映射到10个topic主题模型空间上
doc_lsi = lsi[bow]

['电影', '电影票', '电影票房', '影票', '票房', '给出', '证据', '刘若英', '导演', '处女', '处女作', '预售', '预售票', '售票', '票房', '极佳', '但有', '有人', '利用', '用票', '票务', '平台', '退票', '规则', '便利', '影片', '开映', '前', '恶意', '退票', '武汉', '万达', '几家', '影城', '累计', '退票', '4342', '张']


In [123]:
doc_lsi

[(0, 0.32883976451146707),
 (1, -0.14869293529994107),
 (2, -0.010077540402885318),
 (3, 0.0013473724099843942),
 (4, 0.010133739551352852),
 (5, -0.03592750944927367),
 (6, -0.0073220988243068294),
 (7, 0.032487391387370508),
 (8, 0.028634367668442157),
 (9, -0.041258243510565319)]

In [118]:
sims = index[doc_lsi] # index: similarities.MatrixSimilarity
sims #length: 50000

array([ 0.31384632,  0.57825452,  0.37494934, ...,  0.96670753,
        0.89561689,  0.91552949], dtype=float32)

In [119]:
sort_sims = sorted(enumerate(sims), key=lambda item: -item[1])

In [121]:
for i in [s[0] for s in sort_sims[:10]]:
    print(df_news.iloc[i]['category'])
    print(df_news.iloc[i]['content'])
    print("---------------------------")

时尚
女明星除了拥有才艺外，亮丽的外型更是优先关注的焦点。如果拥有一副混血儿般的外型，不但容易引起瞩目，也容易让观众留下深刻印象。当然想在演艺圈内闯出名号，这些条件容易加分之外，更重要的还是得靠自身的努力，才能获得观众的认同。以下将介绍几位演艺圈混血美女，看看她们目前发展的现况。李嘉欣产后复出，精神奕奕，近日在台湾为某保养品做宣传，１５秒广告中，她只说了“美丽不变”４字，进账千万台币，真的是一字千金。自出道以来，不算拍戏的收入，就只是广告的收入，就足以傲笑巾帼！
---------------------------
娱乐
０８年，萧蔷又传和富商徐嘉森吃饭。当时的报道：萧蔷保养得宜，３９岁的她始终是富商老板的最爱，前晚媒体目击，她抱着爱犬与已婚的和展传播老板徐嘉森相约吃饭，萧大美人娇声嗲气，电得大老板服服贴贴，自动脱下西装外套当起“跑腿小弟”，帮她端菜服务献殷勤。
---------------------------
娱乐
伍佰＆Ｃｈｉｎａ　Ｂｌｕｅ将于９／９推出新专辑《单程车票》，继首支单曲《火山》备受好评后，再推出必定成为最新婚礼指定曲的抒情摇滚情歌《戒指》，ＭＶ中伍佰首次破例邀请女艺人共演。因为欣赏爱纱来台湾奋斗的“勇敢”特质，伍佰请来爱纱饰演ＭＶ女主角，让大家都大吃一惊，和伍佰首次合作，爱纱也紧张到前晚睡不着觉，所幸ＭＶ出炉所有人都竖起大姆指说两人“超级般配”，伍佰和爱纱在ＭＶ中的异国恋情加上亡命天涯的旅程让看过的人都很感动，新歌《戒指》ＭＶ也将于８／３１起在Ｃｈａｎｎｅｌ　［Ｖ］频道首播。为了暌违三年的新辑《单程车票》伍佰决心把时间都留给粉丝及宣传期，推了三部电影片约，８／２７高雄、８／２８台中的演出表演了四首新歌让粉丝“爆炸”，９／２及９／３在华山Ｌｅｇａｃｙ的“今夜伍佰４　Ｌｉｖｅ　Ｈｏｕｓｅ巡回”必定精彩可期，没抢到票的粉丝也不用失望，演出结束后伍佰＆Ｃｈｉｎａ　Ｂｌｕｅ将举办专辑预购签名会，预计２２：００开始，签完为止。
---------------------------
娱乐
大家都知道在台湾被称为“花美男”的郑元畅先生，出道至今近１０年，拍过的电视剧超过１０多部，但大多数都是叫好不叫座，尤其像《蜂蜜幸运草》《热情仲夏》等多部剧收视率都创台湾偶像剧新低。但郑元畅幸运的是遇到了林依晨，并与其拍摄了红遍全亚洲的《恶作剧》系列，这才成功上位到一线

In [74]:
#换用lsi[corpus_tfidf]来构造相似度矩阵
print(datetime.now())
index_tfidf = similarities.MatrixSimilarity(lsi[corpus_tfidf]) #WARNING : scanning corpus to determine the number of features (consider setting `num_features` explicitly)
#dict_size = len(list(dictionary.token2id.keys()))
#index = similarities.MatrixSimilarity(lsi[corpus_tfidf],num_features = dict_size)#num_features (int, optional) – Size of the dictionary.
print(datetime.now())

2018-04-30 16:36:52.804910
2018-04-30 16:39:23.544299


使用corpus_tfidf构造相似度矩阵耗时2分钟左右,添加num_features参数耗时约三分半

In [93]:
#随机取一篇文章来测试
document = contents_list_of_list[29981]
bow = dictionary.doc2bow(document) #bow = corpus[29981]
tfidf_doc = tfidf[bow]
doc_lsi = lsi[tfidf_doc] #相似度矩阵用语料的tfidf值构造的，这里也用文档的tfidf值构造

In [94]:
print(datetime.now())
sims = index_tfidf[doc_lsi] 
sort_sims = sorted(enumerate(sims), key=lambda item: -item[1])
print(datetime.now())
sort_sims[:10]

2018-04-30 16:50:05.755889
2018-04-30 16:50:05.846132


[(29981, 1.0),
 (26403, 0.99526495),
 (28335, 0.99501634),
 (26150, 0.99496186),
 (29395, 0.99496186),
 (28891, 0.99423695),
 (27248, 0.99358702),
 (26241, 0.99325675),
 (28295, 0.9932549),
 (27804, 0.99269474)]

In [95]:
for i in [s[0] for s in sort_sims[:10]]:
    print(df_news.iloc[i]['category'])
    print(df_news.iloc[i]['content'])
    print("---------------------------")

从２００４年至２０１１年，北京高考文理科第一名共有１９人。其中，文科第一名１０人，理科第一名９人。３鱿植⒘忻次的年份共有２年：分别为２００５年和２０１１年。其中２００５年为２位理科头名并列；２０１１年为３位文科头名并列。０凑招员鸹分，第一名呈现阴盛阳衰之势；女性第一名占了绝大多数，共有１４位；除了２００４年第一名全部为男生外，其余年份均有女生；其中还有４年文理头名皆为女生，没有男生。４油访们来自的中学看，共有８位头名来自人大附中（含人大附中分校），其中文科２人，理科６人，除２００６年没有产生文理第一名外，其余年份，人大附中每年都会毫无悬念地产生至少一位头名。３了人大附中外，还有８所学校产生过文理科第一名，这些学校分别位于海淀、西城和东城。４油访们最终选择的高校看，８年来，香港高校与北大、清华争夺高考第一名的激烈程度已进入白热化，１１名头名最终选择在香港高校就读。
---------------------------
天津实施高中新课程改革以来，基础教育的教学质量在稳步提高。今年天津高考命题工作按照“稳中有升”的原则，更加注重考查基础、考查能力，试题内容更加贴近学生、贴近生活，较好体现了新课程标准的要求，文理科平均分数有所提高，考生成绩普遍好於往年。８餮Э破骄成绩分别为：文史类语文１０１．８５分、数学（文）８６．０６分、英语８１．６７分、文科综合１７８．０５分、文史类总平均４４７．６３分﹔理工类语文１０３．４９分、数学（理）９８．１７分、英语９０．８１分、理科综合１７５．８６分、理工类总平均４６８．３３分。Ｌ旖蚋呖几鞣质段统计情况如下？评帻７质＠奂迫耸？评帻７质＠奂迫耸＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉Ｎ氖俘＠砉＠砉＠砉＠砉＠砉＠砉＠砉
---------------------------
泡沫之夏，七月流火，面对悠长夏季，很多备考

结果也还不错，继续用新文档测试下

In [113]:
#构造一篇新文章
document = "根据“电影票房”给出的证据，刘若英的导演处女作《后来的我们》预售票房极佳，但有人利用票务平台可以退票的规则便利，在影片开映前恶意退票，仅武汉万达的几家影城就累计退票4342张。"
content = build_corpus(document,False,delimiter = ',')
print(content)

bow = dictionary.doc2bow(content) 
tfidf_doc = tfidf[bow]
#通过lsi模型将选定的文档映射到10个topic主题模型空间上
doc_lsi = lsi[tfidf_doc]

['电影', '电影票', '电影票房', '影票', '票房', '给出', '证据', '刘若英', '导演', '处女', '处女作', '预售', '预售票', '售票', '票房', '极佳', '但有', '有人', '利用', '用票', '票务', '平台', '退票', '规则', '便利', '影片', '开映', '前', '恶意', '退票', '武汉', '万达', '几家', '影城', '累计', '退票', '4342', '张']


In [114]:
sims = index[doc_lsi] # index: similarities.MatrixSimilarity
sims #length: 50000

array([ 0.28551459,  0.55927753,  0.35080469, ...,  0.96152949,
        0.89655787,  0.91736615], dtype=float32)

In [115]:
sort_sims = sorted(enumerate(sims), key=lambda item: -item[1])

In [116]:
for i in [s[0] for s in sort_sims[:10]]:
    print(df_news.iloc[i]['category'])
    print(df_news.iloc[i]['content'])
    print("---------------------------")

时尚
女明星除了拥有才艺外，亮丽的外型更是优先关注的焦点。如果拥有一副混血儿般的外型，不但容易引起瞩目，也容易让观众留下深刻印象。当然想在演艺圈内闯出名号，这些条件容易加分之外，更重要的还是得靠自身的努力，才能获得观众的认同。以下将介绍几位演艺圈混血美女，看看她们目前发展的现况。李嘉欣产后复出，精神奕奕，近日在台湾为某保养品做宣传，１５秒广告中，她只说了“美丽不变”４字，进账千万台币，真的是一字千金。自出道以来，不算拍戏的收入，就只是广告的收入，就足以傲笑巾帼！
---------------------------
娱乐
自从戚其义搭档编剧周旭明弄了几部看起来重口味的剧集（如《天与地》以及《心战》）之后，资深港剧迷们开始欢呼雀跃，貌似以为看到港剧新一轮的曙光而挺直了腰板。的确，这几部戏较近年大多数的港剧而言，无论品质还是口碑都很不错，但问题是，它们真的能重塑上世纪九十年代的港剧辉煌吗？Ｏ匀徊荒堋Ｒ浴缎恼健肺例，这注定是一部引起关注但收视率偏低的剧集，其中呈现的凶杀、黑色、宗教、隐喻等内容，都过于晦涩，虽然也搞一惊一咋的悬疑，但整体过程比较沉闷，情节跳跃，节奏拖沓，有点Ｂ级片的酷劲，但还远远不够。对于香港的电视播出环境，我个人觉得应该是既开阔又逼仄的。由于没有审查制度，编导自由创作空间很大，可以拍如此暗黑的故事，但问题是，香港仍然是中国文化传统占据主流价值观，中国式家庭妇女（香港称师奶）无论受到的教育还是本身个性，都比较温雅，喜欢的能接受的也多为真善美的东西，换句话说，作为电视剧的主流收视人群，她们更爱看轻松愉悦而非黑色系的剧集。据数据显示，《心战》在经过开播阶段的一阵高起之后，收视率暴跌，基本上和去年的《天与地》遭遇了同样的尴尬。２还现在是网络时代，制片方大可把宝押在网络平台的播出以及年轻观众的热捧上，只要质量拔尖就行。可在我看来，本剧之所有目前受到各方追捧，在于戚其义的品牌效应，再加上港剧普遍质量较差，属于矮子里面拔将军。就剧论剧吧，《心战》通过一个变态杀手之嘴，假借恶魔之说，对社会表达一种批判的姿态：这个世界充满污浊和肮脏，需要通过极端的手段来剪除罪恶，以达到最终的宁静。老实讲，这并非什么高深的道理，仅仅是导演为了让作品看起来有思想性，玩的一个噱头罢了。自《无间道》开始，香港导演就喜欢弄这些看起来有些玄乎深刻实则肤浅不堪的道理，什么炼狱，毁灭，灵魂荡涤啦，诸如

效果也不错